# TP12 exercise

## Deutsch-Jozsa

The Deutsch-Jozsa Algorithm proposed by David Deutsch and Richard Jozsa in 1992,has limited practical use but is one of the first examples of a quantum algorithm, displaying the advantages of working with the quantum paradigm.

This algorithm is deterministic and verifies if a function $f:\{0,1\}^n\rightarrow \{0,1\}$ is balanced or constant.

- **Constant**: its output is always 0 or always 1
- **Balanced**: outputs 0 for half of the input value and 1 for the other half


### Example
(with $n = 2$)

**Constant function**

|input|output|
|-|-|
|000|0|
|001|0|
|010|0|
|011|0|
|100|0|
|101|0|
|110|0|
|111|0|

**Balanced function**

|input|output|
|-|-|
|000|0|
|001|1|
|010|1|
|011|0|
|100|1|
|101|0|
|110|0|
|111|1|


**Balanced function worst case scenario**

|input|output|
|-|-|
|000|0|
|001|0|
|010|0|
|011|0|
|100|1|
|101|1|
|110|1|
|111|1|

We call these functions the **oracle**.

In the example, the oracle takes an input with 3 bits and outputs the unknown value.

To get the answer to this problem in a classical world we may have the worst case scenario which includes testing the function $2^{(n-1)} + 1$ times.

If the evaluations are sequential the worst case scenario needs $2^{(3-1)}+1=5$ tests.

However, **the quantum case only needs one function evaluation**.

### Implementation

Implement the **contant function** of the previous example.

<img src="https://upload.wikimedia.org/wikipedia/commons/b/b5/Deutsch-Jozsa-algorithm-quantum-circuit.png" alt="Note: In order for images to show up in this jupyter notebook you need to select File => Trusted Notebook" width="400 px" align="center">

In [ ]:
from qiskit import *
%matplotlib inline
from qiskit.tools.visualization import *

**1** Initialize the first  $n$  qubits with state  $0$  and a final qubit with state $1$.

$$\lvert \psi_0 \rangle = \lvert 0\rangle^{\oplus n} \lvert 1 \rangle$$

In [ ]:
# Create a quantum circuit with n+1 qubits and n bits
n= 3

qr = QuantumRegister(n+1)
cr = ClassicalRegister(n)
qc = QuantumCircuit(qr,cr)

In [ ]:

qc.draw(output='mpl')

**2** Apply a Hadamard gate to each qubit $H^{\oplus n+1}$.

$$\sum_x \frac{\lvert x \rangle}{\sqrt{2^n}} \left[ \frac{(\lvert 0 \rangle -\lvert 1 \rangle)}{\sqrt{2}} \right]$$

In [ ]:

qc.draw(output='mpl')

**3** Apply the Oracle $f(x)$. 

This maps the state $\lvert x \rangle \lvert y \rangle $ to $ \lvert x \rangle \lvert y \rangle \oplus f(x)\rangle$

$$ \frac{1}{\sqrt{2^{n+1}}} \sum_x \lvert x \rangle (\lvert f(x)\rangle - \lvert 1 \oplus f(x)\rangle )$$

For each $x$, $f(x)$ is either $1$ or $0$ allowing us to rewrite the previews equation as:

$$ \sum_{x} \frac{(-1)^{f(x)} \lvert x \rangle}{\sqrt{2^n}} \left[ \frac{(\lvert 0 \rangle - \lvert 1 \rangle)}{\sqrt{2}} \right] $$

**1 - What is the oracle of the contant function? **

**2- Why?**

 [Tip](https://qiskit.org/textbook/ch-algorithms/deutsch-josza.html#3.-Creating-Quantum-Oracles--)

In [ ]:


qc.draw(output='mpl')

**4** Apply a Hadamard gate to the first $n$ qubits.

$$\sum_{x,y} \frac{(-1)^{f(x) \oplus (x\cdot y)} \lvert x \rangle}{2^n} \left[ \frac{(\lvert 0 \rangle -\lvert 1 \rangle )}{\sqrt{2}} \right]$$

In [ ]:

    
qc.draw(output='mpl')

**5** Measure the first $n$ qubits. The probability of measuring $\lvert 0\rangle \oplus n$:

$$ \left| \sum_x \frac{(-1)^{f(x)}}{2^n} \right| ^2 $$

In [ ]:

    
qc.draw(output='mpl')

*  When $f$ is constant the measure will be $\lvert 0 \rangle^{\otimes n}$;
* When $f$ is balanced the measure will yield any other state.

In [ ]:
backend = Aer.get_backend("qasm_simulator")

In [ ]:
shots=1024
result = execute(qc, backend, shots=shots).result()
counts_sim = result.get_counts(qc)
plot_histogram(counts_sim)

## IBM Q Provider

In [ ]:
provider = IBMQ.load_account()
provider.backends()

In [ ]:
backends_list =provider.backends( simulator=False, open_pulse=False)

In [ ]:
# Backend overview
import qiskit.tools.jupyter

%qiskit_backend_overview

In [ ]:
from qiskit.tools.monitor import backend_overview, backend_monitor

backend_overview()

In [ ]:
from qiskit.providers.ibmq import least_busy

#backend_device = provider.get_backend('ibmq_xxxxxxxx')
#backend_device = least_busy(backends_list)

print("Running on : ", backend_device)

**3 - why did you select this device? **

In [ ]:
# See backend information
backend_device

In [ ]:
backend_monitor(backend_device)

In [ ]:
%qiskit_job_watcher

In [ ]:
#job_DJ_r = execute(qc, backend_device, shots=shots)

jobID_DJ_r = job_DJ_r.job_id()

print('JOB ID: {}'.format(jobID_DJ_r))

In [ ]:
#job_get=backend_device.retrieve_job(" ")
result_DJ_r = job_get.result()
counts_DJ_run = result_DJ_r.get_counts(qc)

In [ ]:
plot_histogram([counts_DJ_run, counts_sim ], legend=[ 'run in real device', 'ideal'], color=['#061727','#82cfff'])

### Optimize

In [ ]:
from qiskit.compiler import transpile

qc_t_real = transpile(qc, backend=backend_device)

qc_t_real.draw(output='mpl', scale=0.5)

In [ ]:
qc_optimized = transpile(qc, backend=backend_device, optimization_level=3)
qc_optimized.draw(output='mpl', scale=0.5)

** 4 - Make a second transpiler optimization, with optimization level 2 or level 1.**

In [ ]:
qc.depth()

In [ ]:
qc_t_real.depth()

In [ ]:
from qiskit.visualization import plot_circuit_layout
plot_circuit_layout(qc_t_real, backend_device)

In [ ]:
qc_optimized.depth()

In [ ]:
plot_circuit_layout(qc_optimized, backend_device)

**5 - What is the layout of the second optimization?**

In [ ]:
#job_exp = execute(qc_optimized, backend_device, shots = shots)

# job_id allows you to retrive old jobs
jobID = job_exp.job_id()

print('JOB ID: {}'.format(jobID))

job_exp.result().get_counts(qc_optimized)

In [ ]:
#job_get_o=backend_device.retrieve_job(" ")
result_real_o = job_get_o.result(timeout=3600, wait=5)

counts_opt = result_real_o.get_counts(qc_optimized)

** 6 - Execute the second optimization**

**7 - Analyse the results**

In [ ]:
%qiskit_disable_job_watcher

In [ ]:
title = 'DJ'
legend = [ 'simulation results','run in real device results', 'optimized circuit level 3', 'optimized circuit level x']

plot_histogram([counts_sim, counts_DJ_run, counts_opt, x], legend = legend, title= title, figsize=(15, 5),)

**Refs**

* [Deutsch-Josza Algorithm - Qiskit](https://qiskit.org/textbook/ch-algorithms/deutsch-josza.html)
* [Lesson 38 Quantum Computing, Deutsch's Problem](https://www.youtube.com/watch?v=5xsyx-aNClM)